# PnL Ratio - long short

Market sentiment is high when everyone is profit on paper, and vice versa. Can we use this as an indicator to trade?

## Comment

The long short strategy do not give better result, or even worse, compared to the follow strategy. This is because the volatility, especially for crypto, will have a much higher volatility during the bear market, and any strategy previously proven to work may suddenly stop working due to the change of volatility. Therefore the best strategy in a bear market is to maintain a low risk profile or even stop trading altogether.

## Data

In [1]:
from btbox import *
from pandas import Series

In [2]:
SYMBOL = 'BTC'
START = '2022-02-01'
WINDOW = 24*30
INTERVAL = 24*3

In [3]:
dfs = {SYMBOL: import_yahoo_csv(f'../../_data_/{SYMBOL}_bar1hour.csv')}

## Benchmark

In [4]:
class BM_AllInAndForget(Strategy):

    def initial(self, b: Broker):
        b.portfolio.trade_target_weight(SYMBOL, 1)


class BM_KeepAtHalf(Strategy):

    @interval(INTERVAL)
    def step(self, b: Broker):
        b.portfolio.trade_target_weight(SYMBOL, 0.5)

## Indicator

In [5]:
def pnl_ratio(win: Series) -> float:
    pnlr = win.rank(pct=True)
    return pnlr[-1]

## Strategy

In [6]:
def ST_LongShortPnL(min, max):

    offset = max - min

    class ST(Strategy):
        name = f'ST_LongShortPnl_range[{min},{max}]'

        @interval(INTERVAL)
        def step(self, b: Broker):
            win = b.market.get_close_window(SYMBOL)
            pnlr = pnl_ratio(win)
            weight = min + offset * pnlr
            b.portfolio.trade_target_weight(SYMBOL, weight)
            self.journal.mark(weight, 'weight')

    return ST

## Backtest

In [7]:
bt = create_backtest(
    [
        BM_AllInAndForget,
        BM_KeepAtHalf,
        ST_LongShortPnL(0, 1),
        ST_LongShortPnL(-0.2, 1),
        ST_LongShortPnL(-0.2, 1.5),
        ST_LongShortPnL(-0.5, 1.5),
    ],
    dfs,
    start=START,
    window=WINDOW,
)

In [8]:
results = bt.run()

## Dashboard

In [9]:
results.dashboard_pretty()

## Equity Curve

In [10]:
results.plot(log_y=True)

## Evaluation

In [11]:
results['ST_LongShortPnl_range[-0.2,1.5]'].journals['weight'].ffill.plot_line_under_price(SYMBOL)